# Exoplanets

## Exoplanet Discovery
For the past 25+ years, NASA has used ground- and space-based methods to [identify exoplanets](https://exoplanets.nasa.gov/exep/about/missions-instruments) (planets outside of our solar system). In the past ten years in particular, campaigns like Kepler, K2, and TESS have produced an explosion of results. To date, over 5,000 exoplanets have been identified, and thousands more potential exoplanet candidates have been discovered. 

In this notebook, we will use [Holoviews](https://holoviews.org) and [Panel](https://panel.holoviz.org) to make a dashboard visualizing the discovery of confirmed and candidate exoplanets over the years.

We'll also include a scatterplot in our dashboard that reveals details about the relationship between mass and radius of exoplanets, as well as controls to filter the data based on whether the planets could support life, and if so, whether chemical rockets could be used to escape the planet.

In [1]:
import pandas as pd
import holoviews as hv
import panel as pn
import numpy as np
import colorcet as cc
import hvplot.pandas # noqa
from scipy import stats

hv.extension('bokeh')

## Loading data
For this notebook, we will be loading our exoplanet data from several different CSV files: 
- [stars1](data/stars1.csv) and [stars2](data/stars2.csv), together forming a [dataset of 257,000 stars](https://www.kaggle.com/solorzano/257k-gaia-dr2-stars?select=257k-gaiadr2-sources-with-photometry.csv) identified by the European Gaia space mission (split into two smaller files so GitHub will let me upload them);
- [exoplanets](data/exoplanets.csv), a collection of over 5600 confirmed exoplanets obtained from the [NASA Exoplanet Archive](https://exoplanetarchive.ipac.caltech.edu/); and 
- [kepler](data/kepler.csv), [k2](data/k2.csv), and [tess](data/tess.csv), a collection of candidate exoplanets collated from the [Kepler](http://exoplanets.org/table?datasets=kepler), [K2](https://exoplanetarchive.ipac.caltech.edu/cgi-bin/TblView/nph-tblView?app=ExoTbls&config=k2pandc), and [TESS](https://exofop.ipac.caltech.edu/tess/view_toi.php) campaigns. 

We could load the data using pure Pandas calls like `stars1 = pd.read_csv('data/stars1.csv')`, but here let's cache the results using Panel so that new visitors to the dashboard won't have to reload or recalculate the data:

In [2]:
%%time
stars1      = pn.state.as_cached('stars1',      lambda: pd.read_csv('data/stars1.csv'))
stars2      = pn.state.as_cached('stars2',      lambda: pd.read_csv('data/stars2.csv'))
stars       = pn.state.as_cached('stars',       lambda: pd.concat([stars1, stars2]))
exoplanets  = pn.state.as_cached('exoplanets',  lambda: pd.read_csv('data/exoplanets.csv'))
kepler      = pn.state.as_cached('kepler',      lambda: pd.read_csv('data/kepler.csv'))
k2          = pn.state.as_cached('k2',          lambda: pd.read_csv('data/k2.csv'))
tess        = pn.state.as_cached('tess',        lambda: pd.read_csv('data/tess.csv'))

CPU times: user 2.1 s, sys: 272 ms, total: 2.37 s
Wall time: 2.62 s


The stars data includes numerous variables, the coordinates (`ra` and `dec`) and brightness (`phot_g_mean_mag`) of the star:

In [3]:
stars.head()

source_id    tycho2_id  parallax  parallax_error  \
0  5781834812959489920   9429-344-1  7.674512        0.023794   
1  6680681063238358528  7953-1368-1  3.206302        0.034306   
2  2065107828836604672  3171-1265-1  3.101280        0.026206   
3  5408451075170077696  8182-1948-1  3.079357        0.030235   
4  5781851958469443584  9429-1241-1  3.225426        0.026983   

   phot_g_mean_mag  phot_rp_mean_mag  phot_bp_mean_mag  \
0        10.113231          9.665930         10.429392   
1        12.095904         11.610787         12.430636   
2        11.209872         10.816037         11.472557   
3        11.566668         11.076862         11.910268   
4        12.487245         11.960208         12.863915   

   phot_g_mean_flux_error          ra        dec  ...  gsc23_b_mag  \
0              640.523864  236.645693 -75.399888  ...       10.869   
1               51.163714  307.362343 -40.700107  ...       12.948   
2              235.630098  313.225036  40.417739  ...       11.817   
3              136.654106  151.755425 -46.530993  ...       12.437   
4               53.066279  235.555713 -75.457647  ...       13.550   

   ppmxl_b1mag  ppmxl_b2mag  ppmxl_r1mag  ppmxl_imag  tmass_j_m  tmass_h_m  \
0        10.71        10.76        10.13       10.19      9.185      8.914   
1        12.66        12.86        11.98       12.32     11.067     10.790   
2        11.38        11.61        11.53       11.27     10.421     10.161   
3        12.29        12.28        11.70       11.57     10.501     10.191   
4        13.05        13.41        12.55       12.77     11.344     11.005   

   tmass_ks_m  tycho2_bt_mag  tycho2_vt_mag  
0       8.849         10.869         10.267  
1      10.715         12.948         12.386  
2      10.113         11.817         11.389  
3      10.101         12.437         11.655  
4      10.966         13.550         12.842  

[5 rows x 36 columns]

The exoplanets data includes the coordinates along with a variety of attributes about the planet. We'll drop unnecessary columns and rename the remaining ones to something clearer:

In [4]:
exoplanets.head()

pl_name  hostname  disc_year  pl_rade   pl_bmasse  pl_insol  pl_eqt  \
0    11 Com b    11 Com       2007     12.2  4914.89849       NaN     NaN   
1    11 UMi b    11 UMi       2009     12.3  4684.81420       NaN     NaN   
2    14 And b    14 And       2008     13.1  1131.15130       NaN     NaN   
3    14 Her b    14 Her       2002     12.6  2559.47216       NaN     NaN   
4  16 Cyg B b  16 Cyg B       1996     13.5   565.73740       NaN     NaN   

          rastr          ra         decstr        dec  
0  12h20m42.91s  185.178779  +17d47m35.71s  17.793252  
1  15h17m05.90s  229.274595  +71d49m26.19s  71.823943  
2  23h31m17.80s  352.824150  +39d14m09.01s  39.235837  
3  16h10m24.50s  242.602101  +43d48m58.90s  43.816362  
4  19h41m51.75s  295.465642  +50d31m00.57s  50.516824

In [5]:
exoplanets = exoplanets.drop(columns=['rastr','decstr']).rename(columns = {
     'pl_name': 'name',
     'pl_rade': 'radius',
     'pl_bmasse': 'mass',
     'pl_insol': 'insolation_flux',
     'pl_eqt': 'temperature',
     'disc_year': 'year'
})

Kepler mission data does not include discovery year or planetary mass. Because Kepler data was collected between 2009 and 2013, we will set `year` to 2013 for all points so they will show up in our final visualization, but it should be noted that this is not quite accurate for every candidate planet in the dataset. Also, we'll rename columns for clarity again.

In [6]:
kepler.head()

kepoi_name  koi_prad  koi_teq         ra        dec
0  K00752.01      2.26    793.0  291.93423  48.141651
1  K00752.02      2.83    443.0  291.93423  48.141651
2  K00753.01     14.60    638.0  297.00482  48.134129
3  K00754.01     33.46   1395.0  285.53461  48.285210
4  K00755.01      2.75   1406.0  288.75488  48.226200

In [7]:
kepler = kepler.rename(columns = {
     'kepoi_name': 'name',
     'koi_prad': 'radius',
     'koi_teq': 'temperature'
})

kepler['year'] = 2013

We'll do the same thing for the K2 and TESS datasets:

In [8]:
k2.head()

pl_name        hostname disposition  disc_year  pl_rade  \
0  EPIC 201111557.01  EPIC 201111557   CANDIDATE       2018    1.120   
1  EPIC 201111557.01  EPIC 201111557   CANDIDATE       2018    1.313   
2  EPIC 201126503.01  EPIC 201126503   CANDIDATE       2016    4.190   
3  EPIC 201127519.01  EPIC 201127519   CANDIDATE       2018    8.840   
4  EPIC 201127519.01  EPIC 201127519   CANDIDATE       2018    9.913   

   pl_bmasse  pl_eqt         rastr          ra         decstr       dec  
0        NaN  1054.0  12h15m23.10s  183.846245  -06d16m05.98s -6.268329  
1        NaN     NaN  12h15m23.10s  183.846245  -06d16m05.98s -6.268329  
2        NaN     NaN  11h43m45.26s  175.938595  -05d52m24.09s -5.873359  
3        NaN   772.0  12h05m29.23s  181.371809  -05d50m53.79s -5.848274  
4        NaN     NaN  12h05m29.23s  181.371809  -05d50m53.79s -5.848274

In [9]:
k2 = k2.drop(columns=['hostname','disposition','rastr','decstr','pl_bmasse']).rename(columns = {
     'pl_name': 'name',
     'pl_rade': 'radius',
     'pl_eqt': 'temperature',
     'disc_year': 'year'
})


In [10]:
tess.head()

TIC ID     TOI CTOI  Master priority  SG1A priority  SG1B priority  \
0  231663901  101.01  NaN                5              5              5   
1  149603524  102.01  NaN                5              5              5   
2  336732616  103.01  NaN                5              5              5   
3  231670397  104.01  NaN                5              5              5   
4  144065872  105.01  NaN                5              5              5   

   SG2 priority  SG3 priority  SG4 priority  SG5 priority  ...  \
0             5             5             5             5  ...   
1             5             5             5             5  ...   
2             5             5             5             5  ...   
3             5             5             5             5  ...   
4             5             5             5             5  ...   

   Stellar Radius error  Stellar Metallicity  Stellar Metallicity error  \
0              0.043847                  NaN                        NaN   
1              0.050000                 0.24                       0.05   
2                   NaN                  NaN                        NaN   
3              0.102573                  NaN                        NaN   
4              0.059699                  NaN                        NaN   

   Stellar Mass (M_Sun)  Stellar Mass error  \
0                  1.05            0.129454   
1                  1.28            0.190812   
2                  1.27            0.196969   
3                  1.16            0.166129   
4                  1.03            0.127209   

                                             Sectors  \
0                                               1,27   
1  1,2,3,4,6,7,8,9,10,11,12,13,27,28,29,30,31,32,...   
2                                                  1   
3                                            1,27,67   
4                                               1,28   

                                Comments Date TOI Alerted (by TESS Project)  \
0                              WASP-46 b                         2018-09-05   
1                              WASP 62 b                         2019-05-07   
2                               HATS-3 b                         2018-09-05   
3                              WASP-73 b                         2018-09-05   
4  WASP-95; epoch kept from qlp-s28-tois                         2018-09-05   

   Date TOI Updated (by TESS Project)  Date Modified (by ExoFOP-TESS)  
0                          2021-10-07                      2022-12-14  
1                          2023-11-16                      2023-12-08  
2                          2020-10-27                      2022-12-14  
3                          2023-10-16                      2023-10-16  
4                          2021-12-08                      2022-12-14  

[5 rows x 61 columns]

TESS data includes precise discovery date, so for consistency with the other datasets, we'll extract the year from that column.

In [11]:
from datetime import datetime

tess = tess.rename(columns = {
    'TIC ID': 'name',
    'RA (deg)': 'ra',
    'Dec (deg)': 'dec',
    'Planet Radius (R_Earth)': 'radius',
    'Planet Eq Temp (K)': 'temperature',
    'Date TOI Alerted (by TESS Project)': 'date'
})[['name','radius','temperature','ra','dec','date']]

tess['year'] = tess['date'].apply(lambda x : datetime.strptime(x,'%Y-%m-%d').year)
tess = tess.drop(columns=['date'])

Now we'll collate all three of the candidate datasets into one DataFrame called `candidates`:

In [12]:
candidates = pd.concat([kepler,k2,tess])
candidates.head()

name  radius  temperature         ra        dec  year
0  K00752.01    2.26        793.0  291.93423  48.141651  2013
1  K00752.02    2.83        443.0  291.93423  48.141651  2013
2  K00753.01   14.60        638.0  297.00482  48.134129  2013
3  K00754.01   33.46       1395.0  285.53461  48.285210  2013
4  K00755.01    2.75       1406.0  288.75488  48.226200  2013

Note that because of imprecise detection methods, characteristics such as temperature, mass, and radius are all estimates. For more information on the uncertainty in these measurements, see the [NASA Exoplanet Archive](https://exoplanetarchive.ipac.caltech.edu/).

Because our goal is to generate a map of the exoplanets and stars, we need a standardized coordinate system for all three of our dataframes. Here, we'll use the [equatorial coordinate system](https://en.wikipedia.org/wiki/Equatorial_coordinate_system) provided in the original datasets. Equatorial coordinates are given by two angles: ``ra`` (right ascension) and ``dec`` (declination). ``ra`` and ``dec`` represent the position of an object on an imaginary sphere called the celestial sphere, with the Earth at its center and an equator that's a projection of the Earth's equator. Right ascension measures the horizontal position of the object on that sphere, and is usually given in either hours or degrees (our datasets use degrees). Declination measures the vertical position of the object. Because these coordinates are defined based on the tilt and shape of the Earth independent of its rotation, the equatorial positions of celestial objects do not change over the course of a day or a year.

In the dataframes, ``dec`` ranges from -90º to 90º and ``ra`` ranges from 0º to 360º. To make our map more intuitive, we will place the Earth at the origin, so we'll need to rewrite the ``ra`` coordinates in the range -180º to 180º. To do this, we'll write a simple function ``recenter``:

In [13]:
def recenter(r):
    "Convert ra coordinates so that Earth is at origin"
    return np.mod(r+180, 360)-180

In [14]:
# Limit to the brightest stars, if desired
#stars = stars[stars["phot_g_mean_mag"]>11]

In [15]:
%%time
stars['ra']      = pn.state.as_cached('stars_ra',      lambda: recenter(stars['ra']))
exoplanets['ra'] = pn.state.as_cached('exoplanets_ra', lambda: recenter(exoplanets['ra']))
candidates['ra'] = pn.state.as_cached('candidates_ra', lambda: recenter(candidates['ra']))

CPU times: user 10.4 ms, sys: 2.45 ms, total: 12.9 ms
Wall time: 11.3 ms



If desired, [Astropy](https://www.astropy.org/) provides methods of converting to other common celestial coordinate systems that can easily be applied to the dataframes.

## The Goldilocks zone

One of the methods used to determine whether an exoplanet could potentially support life is to check whether liquid water could exist there. For water to be present on the planet as liquid, the planet's temperature must be within a fairly narrow range, and therefore the planet must be within a certain distance of the nearest star. Exoplanets within this range are said to be in the "Goldilocks zone." NASA classifies a planet as potentially habitable if its temperature is between 180 K and 310 K or if its insolation (a measure of the heating power of the planet's star) is between 0.25 and 2.2 times Earth's.

Let's create a column in our `exoplanets` DataFrame to represent habitability:

In [16]:
def habitable(temperature, insolation_flux):
    if temperature > 180 and temperature < 310:
        return True
    elif insolation_flux > 0.25 and insolation_flux < 2.2:
        return True
    else:
        return False

exoplanets['habitable'] = exoplanets.apply(lambda x: habitable(x.temperature, x.insolation_flux), axis=1)

We can see that the vast majority of confirmed exoplanets are not in the habitable zone:

In [17]:
exoplanets['habitable'].value_counts()

habitable
False    5440
True      169
Name: count, dtype: int64


## The Tsiolkovsky rocket equation
If intelligent life were to exist on one of these planets, would it be capable of space travel? If the hypothetical life forms used similar methods to humans — for example, hydrogen- and oxygen-powered chemical rockets — would they even be able to leave their planet? A heavier rocket requires exponentially more fuel, but more fuel means more mass. The Tsiolkovsky rocket equation makes this question more precise:

$$\Delta v = v_e\ln\left(\frac{m_0}{m_f}\right),$$

where $\Delta v$ is the [impulse per mass unit](https://en.wikipedia.org/wiki/Impulse_(physics)) required for the rocket to travel its course, $v_e$ is [effective exhaust velocity](https://en.wikipedia.org/wiki/Specific_impulse#Specific_impulse_as_effective_exhaust_velocity), $m_0$ is the initial mass of the rocket, and $m_f$ is the final mass of the rocket (here, equal to $m_0$ minus the mass of the fuel spent on the flight). To see the rocket equation in action, consider a planet of the same density as Earth with radius $R$ double Earth's and thus mass $M$ eight times Earth's. 
<p></p>

<details><summary><i><u>(Click to expand/collapse computation details)</u></i></summary>
    
For the purposes of this example, we'll assume that $$\Delta v = \sqrt{\frac{GM}{R}},$$ where $G\approx 6.67\cdot 10^{-11}$ (in reality, some complicating factors exist, but our formula works as an approximation at relatively low altitudes$^*$). Then

$$\Delta v = \sqrt{\frac{6.67\cdot 10^{-11}\cdot 4.78\cdot10^{25}}{1.27\cdot10^7}}\approx 22407 \frac{\text{m}}{\text{s}}.$$

Using the [highest recorded exhaust velocity of a chemical rocket](https://en.wikipedia.org/wiki/Tripropellant_rocket#:~:text=In%20the%201960s%2C%20Rocketdyne%20fired,for%20a%20chemical%20rocket%20motor.), $5320\frac{\text{m}}{\text{s}},$ and we'll calculate the approximate percent of the rocket's mass that would have to be fuel in order to propel the rocket to $250$ m$^*$:

$$22407= 5320 \ln\left(\frac{m_0}{m_f}\right),$$

so

$$\frac{m_0}{m_f}\approx 67.5.$$

$^*$We won't go into detail here, but the $\Delta v$ calulation for $250$ m is derived from the [vis-viva equation](https://en.wikipedia.org/wiki/Vis-viva_equation).</details>

To make it to $250$ m above this planet's surface, about $98.5\%$ of the rocket's initial mass would need to be fuel. For comparison, the rocket with the highest initial-to-final mass ratio ever built was the [Soyuz-FG](https://en.wikipedia.org/wiki/Soyuz-FG) rocket, which was $91\%$ fuel by mass. Moreover, we were very generous with the conditions used to compute the mass ratio to escape our imaginary planet. The exhaust velocity we used was only ever recorded for a highly corrosive, dangerous, expensive propellant that, with the current state of technology, is not feasible for use in space travel.

## Filtering by feasibility of space travel

We can use the rocket equation to get an idea which exoplanets might be the right size to allow for space travel. Let's assume that the hypothetical life forms on an exoplanet can make a chemical rocket with exhaust velocity at most $5320\frac{\text{m}}{\text{s}}.$ Let's also say that they've figured out how to make rockets that are up to $95\%$ fuel by mass (so $\frac{m_0}{m_f}=20$). These two (generous) assumptions will allow us to make an educated guess of whether the mass and radius of the exoplanet would ever conceivably allow for space travel:

$$\sqrt{\frac{GM}{R}}\approx \Delta v \leq 5320\ln{20}.$$

We can now define a function  ``deltav`` that approximates $\Delta v$ for each exoplanet and returns ``True`` or ``False`` depending on whether that value is small enough. We'll then add a corresponding column ``escapable`` in our dataframe and cache it.

In [18]:
def deltav(p):
    """
    Given a planet record or planet dataframe, determine whether delta-v is 
    sufficiently small for feasible space travel with chemical rockets
    """
    G = 6.67*(10**(-11))
    return np.logical_and(p.habitable, np.sqrt(G*p.mass/p.radius)<=5320*np.log(20))

exoplanets['escapable'] = pn.state.as_cached('escapable', lambda: deltav(exoplanets))

## Filtering and plotting data

To help a user understand the data, we'll allow them to filter it and then plot the results.

To orient users, we'll first create a point representing the Earth at the origin $(0,0)$:

In [19]:
origin = pd.DataFrame(data = {'ra':[0],'dec':[0]})

opts  = dict(x='ra', y='dec', xlabel='right ascension (deg)', ylabel='declination (deg)', 
             responsive=True, aspect=5/2)
earth = hv.Text(0, 0, '🌎', fontsize=20)
# earth

We could plot that single point by itself, but let's go ahead and overlay it on a background of stars as a frame of reference, setting ``rasterize=True`` to use [Datashader](https://datashader.org) to pre-rasterize the data so that it is practical to display in a web browser. We'll also add an arrow with the text "You are here" pointing to the Earth for this display.

In [20]:
star_bg = stars.hvplot.points(
    rasterize=True, color='phot_g_mean_mag', cmap=cc.fire, colorbar=True, cnorm='eq_hist', 
    clabel='G-band mean magnitude', **opts).opts(bgcolor='black')

arrow = hv.Arrow(-5, 0, 'You are here', '>').opts(arrow_color='white',text_color='white',
                                                  text_baseline='top',arrow_line_width=2)

star_bg * earth * arrow

:DynamicMap   []
   :Overlay
      .Image.I :Image   [ra,dec]   (ra_dec phot_g_mean_mag)
      .Text.I  :Text   [x,y]
      .Arrow.I :Arrow   [x,y]

Note that since equatorial coordinates represent the view from the earth, and we are projecting onto a two-dimensional plot, we should imagine the mapped stars wrapping around the Earth spherically, with those with ``ra`` coordinates close to 180º and -180º close to each other. Note also that distances in this map are not reflective of actual distance, but instead of relative position on the celestial sphere (i.e., their relative position as seen from Earth).


One of the first things that jumps out about this plot is the dark curve separating the two clusters of stars. This dark curve represents the [ecliptic](https://earthsky.org/space/what-is-the-ecliptic), the circular tilted path the sun appears to travel in the Earth's sky, projected onto a plane. Few stars lie on this path due to [Gaia's imaging methods](https://gea.esac.esa.int/archive/documentation/GDR2/Introduction/chap_cu0int/cu0int_sec_mission/cu0int_ssec_scanning_law.html#SSS2), which cause the spacecraft to observe the areas near this plane less frequently than other areas.

Now let's plot the planets at their equatorial coordinates, using the point size and color to show attributes about them. When "mass" or "temperature" is selected as the size, we'll scale the points down to 0.5% of the corresponding numerical mass or temperature value, so that planets with large masses or high temperatures do not overwhelm the plot. The sizes are thus mainly for relative scale, though a numerical legend could be provided with a bit of work. When plots are colored by a variable, planets for which that variable is not known will be colored grey.

Note that although most of the exoplanets have radii larger than Earth's, in our plot, the point `earth` is scaled to 20 times its actual size relative to the exoplanets; without this magnification, Earth wouldn't be easily discernible among the other planets.

In [21]:
def planets(planets=exoplanets, size='radius', color='radius'):
    size_scale = 1 if size == 'radius' else 0.005    
    return planets.hvplot.points(color=color, cmap='blues', size=size_scale*hv.dim(size), clabel=color, 
                                 **opts, alpha=0.7)

planets()

:Points   [ra,dec]   (radius)

Two notable features of this graphic are the large, dark blue planet and the dense cluster of smaller planets on the left. The largest planet is the gas giant [HD 100546 b](https://exoplanets.nasa.gov/exoplanet-catalog/6713/hd-100546-b/), with a radius of approximately 77 times that of Earth, and by far the largest exoplanet in our dataset. The clustering behavior on the left is due to the method of detection used in the Kepler mission; the spacecraft pointed at only a small section of the sky, so the detected exoplanets are concentrated in that area.

If we like, we can filter this plot by year and/or by whether it is potentially habitable:

In [22]:
def habitable_exoplanets_by_year(year_range=(-np.inf, np.inf), hab=False):
    "Exoplanets filtered by the given year range and (if hab=True) whether they are habitable"
    e = exoplanets
    filtered = e[(e.year>=year_range[0]) & (e.year<=year_range[1])]
    if hab:
        filtered = filtered[filtered.habitable == True].drop_duplicates()
    filtered = filtered.drop_duplicates()
    return filtered

planets(habitable_exoplanets_by_year((1996, 2021), True))

:Points   [ra,dec]   (radius)

There aren't a lot of potentially habitable exoplanets, and most of them are small and lie in the cluster detected by Kepler. We can also filter by whether the planet is potentially escapable with a chemical rocket, which leaves even fewer! We'll circle those points with a large purple-colored ring so that you can spot them.

In [23]:
def escapable(planets=exoplanets, size='radius', color='radius'):
    escapable = planets[planets['escapable']==True]
    return escapable.hvplot.points(
        cmap='blues', size=200, alpha=0.5, color='purple', line_width=3, fill_color=None, clabel=color, **opts)
    
escapable()

:Points   [ra,dec]

Separately, we can look at the candidate exoplanets to see how their distribution compares with the confirmed exoplanets:

In [24]:
def unconfirmed(year_range=(-np.inf,np.inf)):
    "Filter candidate exoplanets by year range and plot them in b,l space"
    c = candidates
    filtered_candidates = c[(c.year>=year_range[0]) & (c.year<=year_range[1])]
    return filtered_candidates.hvplot.points(size=30, color='green', alpha=0.5, **opts)

unconfirmed()

:Points   [ra,dec]

Again, we see a dense cluster of candidate exoplanets on the right due to the Kepler spacecraft's area of detection, as well as a curve indicating the ecliptic.

Given that all the above plots share the same x and y axes, we can combine them into a single plot so that you can see everything in context:

In [25]:
star_bg * planets() * unconfirmed() * escapable() * earth

:DynamicMap   []
   :Overlay
      .Image.I    :Image   [ra,dec]   (ra_dec phot_g_mean_mag)
      .Points.I   :Points   [ra,dec]   (radius)
      .Points.II  :Points   [ra,dec]
      .Points.III :Points   [ra,dec]
      .Text.I     :Text   [x,y]

Whew, that's a bit of a mess! For a user to make much sense of that, we'll need to let them decide what they want to see dynamically; otherwise it's too difficult to see what's what. Later on we'll see how to define some widgets that let them do that. 

## Radius vs. mass

First, though, let's define a completely different type of visualization, a scatterplot that lets us compare various quantities against each other so that we can see how habitable and uninhabitable exoplanets relate to each other. We'll also include a regression line along with r- and p-values to indicate correlations using the `linregress` function in the `scipy.stats` module. To do this, we'll need to drop all points that do not include our desired measurements.

In [26]:
def scatter(x_axis='radius', y_axis='mass'):
    
    plottable_points = exoplanets.dropna(subset=[x_axis, y_axis])
    slope, y_intercept, r, p, std_err = stats.linregress(plottable_points[x_axis], plottable_points[y_axis])
    
    label_position_x = 0.9*max(plottable_points[x_axis])
    label_position_y = min(plottable_points[y_axis])
    
    regression_line  = hv.Slope(slope,y_intercept).opts(color='black', line_width=3)
    regression_label = hv.Text(label_position_x,label_position_y,f'r = {"%.2f"%(r)}, p = {"%.2e"%(p)}')


    habitable     = plottable_points[plottable_points['habitable']==True]
    uninhabitable = plottable_points[plottable_points['habitable']==False]
    
    habitable_points = habitable.hvplot.scatter(
        x=x_axis,y=y_axis, color='red', responsive=True, aspect=5/2,
        label='Potentially habitable', size=30, legend='top_right')
    
    uninhabitable_points = uninhabitable.hvplot.scatter(
        x=x_axis, y=y_axis, responsive=True, aspect=5/2,
        color='blue', alpha=0.5, legend='top_right',
        label='Uninhabitable', size=10)

    
    return (uninhabitable_points * 
            habitable_points * 
            regression_line * 
            regression_label).opts(
        min_height=400, max_height=600, title=f'Scatterplot of {x_axis} and {y_axis}'
    )

scatter()

:Overlay
   .Scatter.Uninhabitable         :Scatter   [radius]   (mass)
   .Scatter.Potentially_habitable :Scatter   [radius]   (mass)
   .Annotation.I                  :Slope   [x,y]
   .Text.I                        :Text   [x,y]

In the plot above, we can see that most planets have a mass under 15,000 times Earth's and radii under 25 times Earth's, but there are a few outliers. The exoplanet with the largest mass in our dataset is the gas giant [Kepler-297 d](https://exoplanets.nasa.gov/exoplanet-catalog/8849/kepler-297-d/), whose mass is over 89,000 times Earth's, and whose radius is only about 33 times Earth's.

[HD 100546 b](https://exoplanets.nasa.gov/exoplanet-catalog/6713/hd-100546-b/) has the largest radius compared to Earth's, dwarfing our planet by a factor of 77 (that's the big blue planet in the `planets()` plot). On the other side of the scale, the smallest planet in radius is [Kepler-37 b](https://exoplanets.nasa.gov/exoplanet-catalog/1823/kepler-37-b/), whose radius is a third of Earth's, but whose mass is quadruple Earth's.

The hottest planet in our dataset is the gas giant [KELT-9 b](https://exoplanets.nasa.gov/exoplanet-catalog/3508/kelt-9-b/), whose surface temperature is 4050 Kelvin, and the coldest is [MOA-2007-BLG-400L b](https://exoplanets.nasa.gov/exoplanet-catalog/6096/moa-2007-blg-400l-b/), at only 34 Kelvin. Temperature and radius appear to have a positive correlation.

In terms of habitability, all the potentially habitable exoplanets have radius less than 15 times Earth's, and most have mass less than 100 times Earth's.

Linear regression gives us a significant positive relationship among all three variables. The shape of the plot of radius versus temperature suggests that our data may be clustered, an interesting avenue for possible future analysis.

## Dashboard

Now that we have our data and plots defined, we can use Panel widgets and layouts to build a shareable dashboard where we can explore all the combinations. 

First, we'll define two dropdown menus to choose the axis variables for the scatter plot:

In [27]:
axis_choices={'Earth radius':'radius', 'Earth mass': 'mass', 'Temperature': 'temperature'}

x_axis = pn.widgets.Select(name='x-axis:', options=axis_choices)
y_axis = pn.widgets.Select(name='y-axis:', options=axis_choices, value='mass')

Widgets need to be bound to a function or other dynamic object for them to have any effect. Here, we'll use ``pn.bind`` to bind the user's axis selections to the arguments needed by our plotting function, then display the result along with the widgets:

In [28]:
bound_scatter = pn.bind(scatter, x_axis=x_axis, y_axis=y_axis)

pn.Column(pn.Row(x_axis, y_axis), bound_scatter)

Column
    [0] Row
        [0] Select(name='x-axis:', options={'Earth radius': 'radius',...}, value='radius')
        [1] Select(name='y-axis:', options={'Earth radius': 'radius',...}, value='mass')
    [1] ParamFunction(function, _pane=HoloViews, defer_load=False)

We can add other widgets controlling the map, including a slider representing discovery year, a checkbox determining whether to show unconfirmed exoplanets, a second checkbox determining whether to display only planets in the potentially habitable zone, and two dropdown menus to determine what the size and color of the points on the plot will represent:

In [29]:
year_range       = pn.widgets.RangeSlider( name='Discovery year range', start=1996, end=2024)
show_unconfirmed = pn.widgets.Checkbox(    name='Show unconfirmed exoplanets')
show_habitable   = pn.widgets.Checkbox(    name='Limit to potentially habitable planets')
show_escapable   = pn.widgets.Checkbox(    name='Show which planets could be escaped with a chemical rocket')
select_size      = pn.widgets.Select(      name='Size points by:',  options=axis_choices)
select_color     = pn.widgets.Select(      name='Color points by:', options=axis_choices)

widgets = pn.Column(
    pn.Row(
        pn.Column(select_size, select_color),
        pn.Column(year_range, show_unconfirmed, show_escapable, show_habitable)))

#widgets

We'll first bind the filtering widgets to the arguments of our filtering function to generate a dynamically filtered dataframe that will be used in multiple plots:

In [30]:
filtered = pn.bind(habitable_exoplanets_by_year, year_range, show_habitable)

Now we can bind this dataframe and the other widgets to the various plotting function arguments. We'll wrap the bound functions as [HoloViews DynamicMaps](https://holoviews.org/reference/containers/bokeh/DynamicMap.html) so that we can use the HoloViews `*` overlay operator on them:

In [31]:
overlay = (star_bg * 
           hv.DynamicMap(pn.bind(planets,     filtered, select_size, select_color)) * 
           hv.DynamicMap(pn.bind(unconfirmed, year_range)).apply.opts(visible=show_unconfirmed) *
           hv.DynamicMap(pn.bind(escapable,   filtered, select_size, select_color)).apply.opts(visible=show_escapable) * 
           earth).opts(title='Map of exoplanets', min_height=400, max_height=600)
#overlay

## Putting it all together
Finally, we create a panel from our widgets and plots to display the final dashboard using a [Panel template](https://panel.holoviz.org/reference/index.html#templates).

In [32]:
explorer = pn.Row(pn.Column(widgets, overlay, pn.Row(x_axis, y_axis), bound_scatter))

dashboard = pn.template.BootstrapTemplate(title='Exoplanets Explorer')
dashboard.main.append('Filter, color, and size the displayed exoplanets using the available widgets, and explore trends in the scatterplot below.')

dashboard.main.append(explorer)
dashboard.servable()

explorer

Row
    [0] Column
        [0] Column
            [0] Row
                [0] Column
                    [0] Select(name='Size points by:', options={'Earth radius': 'radius',...}, value='radius')
                    [1] Select(name='Color points by:', options={'Earth radius': 'radius',...}, value='radius')
                [1] Column
                    [0] RangeSlider(end=2024, name='Discovery year range', start=1996, step=1, value=(1996, 2024), value_end=2024, value_start=1996)
                    [1] Checkbox(name='Show unconfirmed e...)
                    [2] Checkbox(name='Show which planets c...)
                    [3] Checkbox(name='Limit to potentially h...)
        [1] HoloViews(DynamicMap, sizing_mode='scale_both')
        [2] Row
            [0] Select(name='x-axis:', options={'Earth radius': 'radius',...}, value='radius')
            [1] Select(name='y-axis:', options={'Earth radius': 'radius',...}, value='mass')
        [3] ParamFunction(function, _pane=HoloViews, defer_load=False)

You can use this app here in the notebook, or serve it as a standalone dashboard using a command like `panel serve --show exoplanets.ipynb`.